# Tutorial: Graphistry for Developers


**Start by generating interactive graphs in the [Analysis tutorial](https://github.com/graphistry/pygraphistry/demos/for_analysis.ipynb)**


**Graphistry is a client/server system:**

  * Graphs are akin to live documents: they are created on the server (a `dataset`), and then users can interact with them
  * Uploads may provide some settings
  * Users may dynamically create settings, such as filters: these are `workbooks`. Multiple `workbooks` may reuse the same `dataset`


**APIs:**

  - Backend APIs
    - [Python](https://github.com/graphistry/pygraphistry)
    - [REST](https://hub.graphistry.com/docs/api/)
    - [NodeJS](https://graphistry.github.io/graphistry-js/node-tsdocs/)
  - Frontend APIs
    - iframe
    - React
    - JavaScript

In [4]:
import graphistry

# To specify Graphistry account & server, use:
# graphistry.register(api=3, username='...', password='...', protocol='https', server='hub.graphistry.com')
# For more options, see https://github.com/graphistry/pygraphistry#configure

## 1. Backend APIs

Graphistry provides a REST upload API, and you can reuse the Python client for more conveniently using it.

### Python
* Use the PyGraphistry API as in the [Analysis tutorial](https://github.com/graphistry/pygraphistry/demos/for_analysis.ipynb)
* Instead of plotting, get the plot URL for embedding


In [34]:
edges = [{'src': 0, 'dst': 1}, {'src': 1, 'dst': 0}]

g = graphistry.edges(pd.DataFrame(edges)).bind(source='src', destination='dst').settings(url_params={'play': 1000})

url = g.plot(render=False)

url

u'https://hub.graphistry.com/graph/graph.html?dataset=PyGraphistry/D1I2OZFIZR&type=vgraph&viztoken=1b70c86e6b6f357d435dce80bf37c42ce284c6ae&usertag=86f11264-pygraphistry-0.9.63&splashAfter=1554622313&info=true&play=1000'

### REST
* Sample CURL below
* Get API key either from your profile page, or for admins, by [generating a new one]( https://github.com/graphistry/graphistry-cli)

In [1]:
json_data = {
    "name": "myUniqueGraphName",
    "type": "edgelist",
    "bindings": {
        "sourceField": "src",
        "destinationField": "dst",
        "idField": "node"
    },
    "graph": [
      {"src": "myNode1", "dst": "myNode2",
       "myEdgeField1": "I'm an edge!", "myCount": 7},
      {"src": "myNode2", "dst": "myNode3",
        "myEdgeField1": "I'm also an edge!", "myCount": 200}
    ],
    "labels": [
      {"node": "myNode1",
       "myNodeField1": "I'm a node!",
       "pointColor": 5},
      {"node": "myNode2",
       "myNodeField1": "I'm a node too!",
       "pointColor": 4},
      {"node": "myNode3",
       "myNodeField1": "I'm a node three!",
       "pointColor": 4}
    ]
}

import json
with open('./data/samplegraph.json', 'w') as outfile:  
    json.dump(json_data, outfile)

In [2]:
! curl -H "Content-type: application/json" -X POST -d @./data/samplegraph.json https://hub.graphistry.com/etl?key=YOUR_API_KEY_HERE

{"success":true,"dataset":"myUniqueGraphName"}

### NodeJS
See  [@graphistry/node-api](https://graphistry.github.io/graphistry-js/node-tsdocs/) docs


## 2. Frontend APIs

Graphistry supports 3 frontend APIs: iframe, React, and JavaScript

### iframe

In [27]:
from IPython.display import HTML, display

#skip splash screen
url = url.replace('splashAfter', 'zzz')

display(HTML('<iframe src="' + url + '" style="width: 100%; height: 400px"></iframe>'))

### JavaScript - Browser vanilla JS
* [npm](https://www.npmjs.com/package/@graphistry/client-api)
* `npm install --save "@graphistry/client-api"`
* See [vanilla js examples](https://hub.graphistry.com/static/js-docs/examples/toggles.html)]
* Try with [RunKit](https://npm.runkit.com/@graphistry/client-api)

The JavaScript API uses RxJS Observables. Icons are via [Font Awesome 4](https://fontawesome.com/v4.7.0/icons/).


```
var pointIconEncoding = {
    attribute: 'type',
    mapping: {
       categorical: {
           fixed: {
               'Page': 'file-text-o',
               'Phone': 'mobile',
               'Email': 'envelope-o',
               'Instagram': 'instagram',
               'Snapchat': 'snapchat',
               'Twitter': 'twitter',
               'Location': 'map-marker',
           }
       }
    }
};

var pointColorEncoding = {
    attribute: 'type',
    mapping: {
       categorical: {
           fixed: {
               'Page': '#777777',
               'Phone': '#f8999e',
               'Email': '#c05c61',
               'Username': '#00AA00',
               'Instagram': '#a43cb1',
               'Snapchat': '#fffb2e',
               'Twitter': '#46a6e4',
               'Location': '#9c4e00',
               'Facebook': '#3f5692',
               'Telegram': '#37aee2'
           },
          'other': '#cccccc'
       }
    }
};

document.addEventListener("DOMContentLoaded", function () {

    GraphistryJS(document.getElementById('viz'))
        .flatMap(function (g) {
            window.g = g;
            g.updateSetting('pointSize', 3);
            g.encodeIcons('point', 'type', pointIconEncoding.mapping);
            return g.encodeColor('point', 'type', 'categorical', pointColorEncoding.mapping);
        })
        .subscribe(function (result) {
            console.log('all columns: ', result);
        }, function(result) {
            console.log('error', result);
        });
});
```

## JavaScript React

The React API wraps the JavaScript API.

* [npm](https://www.npmjs.com/package/@graphistry/client-api-react)
* `npm install --save "@graphistry/client-api-react"`
* See [examples](https://hub.graphistry.com/static/js-docs/index.html)
* See [sample CRA project](https://github.com/graphistry/graphistry-js/tree/master/projects/cra-test-18)
* See [options](https://github.com/graphistry/graphistry-js/blob/master/projects/client-api-react/src/bindings.js)

```
import { Graphistry } from '@graphistry/client-api-react';

<Graphistry
    key={react_nonce}
    className={'my_class'}
    vizClassName={'my_class_2'}
    
    defaultPointsOfInterestMax={20}
    defaultPruneOrphans={true}
    defaultShowPointsOfInterest={true}
    defaultShowPointsOfInterestLabel={false}
    backgroundColor={'#EEEEEE'}
    defaultPointSize={1}
    defaultDissuadeHubs={true}
    defaultGravity={8}
    defaultScalingRatio={12}
    defaultEdgeOpacity={0.5}
    defaultShowArrows={false}
    defaultEdgeCurvature={0.02}
    defaultShowLabelPropertiesOnHover={true}
    ...
    play={2000}
    showIcons={true}
    defaultShowToolbar={true}
    axes={axes}
    controls={controls}
    type={datasetType}
    dataset={datasetName}
    graphistryHost={'http://...'}
    loadingMessage={'loading..'}
    showLoadingIndicator={true}
/>
```


